In [2]:
import pandas as pd

In [2]:
CtFamPens = 0.8
NroBenAno = 13
FtBenEnti = 0.98
FtBenLiquido = 1
peculioMorteAssistido = 11.62
perct_saque_bua = 0
perct_opcao_bua = 0
CdPlanBen = 5
teto_contribuicao_inss = 5481.59
faixa_1 = 0
faixa_2 = 0
faixa_3 = 0

In [12]:
def calcular_beneficio_total_atc(row):
    benef_total_atc = 0
    
    if CdPlanBen == 1:
        benef_total_atc = max(0, row['SalConPrjEvol'] - row['SalProjeInssEvol'])

        if row['PeFatReduPbe'] > 0:
            benef_total_atc = max(0, benef_total_atc * row['PeFatReduPbe'])

        FtRenVitAtc = max(0, (row['axcb'] + CtFamPens * row['PrbCasado'] * (row['ajxcb'] - row['ajxx'])) * NroBenAno * FtBenEnti)

        if FtRenVitAtc > 0:
            benef_total_atc = max(benef_total_atc, ((row['VlSdoConPartEvol'] + row['VlSdoConPatrEvol']) / FtRenVitAtc) * FtBenEnti)
    elif CdPlanBen == 2:
        benef_total_atc = max(0, row['VlBenSaldado'] * FtBenLiquido * FtBenEnti)
    elif CdPlanBen == 4 or CdPlanBen == 5:
        FtRenVitAtc = max(0, (row['axcb'] + CtFamPens * row['PrbCasado'] * (row['ajxcb'] - row['ajxx'])) * NroBenAno * FtBenEnti + (row['Ax'] * peculioMorteAssistido))

        if FtRenVitAtc > 0:
            benef_total_atc = max(0, ((row['VlSdoConPartEvol'] + row['VlSdoConPatrEvol']) / FtRenVitAtc) * FtBenEnti)
            
    return round(benef_total_atc, 2)

In [13]:
def calcular_contribuicao(beneficio, teto_contribuicao_inss, faixa_1, faixa_2, faixa_3):
    contribuicao = 0

    if CdPlanBen == 1:
        contr1, contr2, contr3 = 0

        contr1 = min(beneficio, teto_contribuicao_inss / 2) * faixa_1

        if (beneficio > (teto_contribuicao_inss / 2)):
            contr2 = (min(beneficio, teto_contribuicao_inss) - (teto_contribuicao_inss / 2)) * faixa_2

        if (beneficio > teto_contribuicao_inss):
            contr3 = (beneficio - teto_contribuicao_inss) * faixa_3

        contribuicao = contr1 + contr2 + contr3

    return round(contribuicao, 2)

In [14]:
def calcular_beneficio_liquido_atc(beneficio_total, contribuicao, perct_opcao_bua, perct_saque_bua):
    benef_liquido_atc = max(0, (beneficio_total - contribuicao) * (1 - perct_opcao_bua * perct_saque_bua))
    return round(benef_liquido_atc, 2)

In [3]:
ativo_fluxo_atc = pd.read_csv("input_csv/30318/fluxo_atc.csv", sep=",", decimal=".")

In [6]:
ativo_fluxo_atc['BenLiqCobATC'] = [float(x.replace(".","").replace(",", ".")) for x in ativo_fluxo_atc['BenLiqCobATC']]

In [9]:
ativo_fluxo_atc['BenTotCobATC'] = [float(x.replace(".","").replace(",", ".")) for x in ativo_fluxo_atc['BenTotCobATC']]

In [11]:
ativo_fluxo_atc['VlSdoConPartEvol'] = [float(x.replace(".","").replace(",", ".")) for x in ativo_fluxo_atc['VlSdoConPartEvol']]

In [12]:
ativo_fluxo_atc['VlSdoConPatrEvol'] = [float(x.replace(".","").replace(",", ".")) for x in ativo_fluxo_atc['VlSdoConPatrEvol']]

In [8]:
ativo['VlBenSaldado'] = [float(x.replace(".","").replace(",", ".")) for x in ativo['VlBenSaldado']]

In [13]:
ativo_fluxo_atc.dtypes

ID_PARTICIPANTE       int64
tCobertura            int64
tDeterministico       int64
BenLiqCobATC        float64
BenTotCobATC        float64
PrbCasado           float64
VlSdoConPartEvol    float64
VlSdoConPatrEvol    float64
px                  float64
pxs                 float64
axcb                float64
apx                 float64
ajxcb               float64
ajxx                float64
Ax                  float64
taxa_juros_cob      float64
taxa_juros_det      float64
dtype: object

In [14]:
ativo_fluxo_atc.describe()

ID_PARTICIPANTE    tCobertura  tDeterministico  BenLiqCobATC  \
count     5.932207e+06  5.932207e+06     5.932207e+06  5.932207e+06   
mean      1.341182e+07  2.253622e+01     4.507244e+01  3.974477e+01   
std       7.185625e+02  1.633277e+01     1.642742e+01  2.728607e+02   
min       1.341059e+07  0.000000e+00     0.000000e+00  0.000000e+00   
25%       1.341120e+07  9.000000e+00     3.300000e+01  0.000000e+00   
50%       1.341182e+07  2.000000e+01     4.800000e+01  0.000000e+00   
75%       1.341244e+07  3.400000e+01     5.900000e+01  0.000000e+00   
max       1.341309e+07  7.600000e+01     7.600000e+01  5.339170e+03   

       BenTotCobATC     PrbCasado  VlSdoConPartEvol  VlSdoConPatrEvol  \
count  5.932207e+06  5.932207e+06      5.932207e+06      5.932207e+06   
mean   3.974477e+01  7.736695e-01      5.750978e+01      5.585964e+01   
std    2.728607e+02  1.151359e-01      3.316688e+03      3.218423e+03   
min    0.000000e+00  6.000000e-01      0.000000e+00      0.000000e+00   
25%    0.000000e+00  6.000000e-01      0.000000e+00      0.000000e+00   
50%    0.000000e+00  8.500000e-01      0.000000e+00      0.000000e+00   
75%    0.000000e+00  8.500000e-01      0.000000e+00      0.000000e+00   
max    5.339170e+03  8.500000e-01      5.544406e+05      5.489777e+05   

                 px        pxs          axcb           apx         ajxcb  \
count  5.932207e+06  5932207.0  5.932207e+06  5.932207e+06  5.932207e+06   
mean   2.539024e-01        1.0  3.333314e+00  9.982558e-01  1.837101e-01   
std    3.401463e-01        0.0  2.768346e+00  4.172728e-02  1.291680e+00   
min    0.000000e+00        1.0  0.000000e+00  0.000000e+00  0.000000e+00   
25%    5.760900e-04        1.0  2.074452e+00  1.000000e+00  0.000000e+00   
50%    4.276275e-02        1.0  2.402871e+00  1.000000e+00  0.000000e+00   
75%    4.767216e-01        1.0  4.150645e+00  1.000000e+00  0.000000e+00   
max    1.000000e+00        1.0  1.551571e+01  1.000000e+00  1.619500e+01   

               ajxx            Ax  taxa_juros_cob  taxa_juros_det  
count  5.932207e+06  5.932207e+06    5.932207e+06    5.932207e+06  
mean   1.251342e-01  1.818441e-02    5.510000e-02    5.510000e-02  
std    9.578371e-01  1.139183e-01    1.956012e-12    1.956012e-12  
min    0.000000e+00  0.000000e+00    5.510000e-02    5.510000e-02  
25%    0.000000e+00  0.000000e+00    5.510000e-02    5.510000e-02  
50%    0.000000e+00  0.000000e+00    5.510000e-02    5.510000e-02  
75%    0.000000e+00  0.000000e+00    5.510000e-02    5.510000e-02  
max    1.446925e+01  9.477775e-01    5.510000e-02    5.510000e-02

In [15]:
ativo_fluxo_atc.head()

ID_PARTICIPANTE  tCobertura  tDeterministico  BenLiqCobATC  BenTotCobATC  \
0         13410587           0                0       1570.79       1570.79   
1         13410587           0                1       1570.79       1570.79   
2         13410587           0                2       1570.79       1570.79   
3         13410587           0                3       1570.79       1570.79   
4         13410587           0                4       1570.79       1570.79   

   PrbCasado  VlSdoConPartEvol  VlSdoConPatrEvol        px  pxs       axcb  \
0        0.6         156073.53          150133.2  1.000000  1.0  14.273423   
1        0.6              0.00               0.0  0.997528  1.0  14.065947   
2        0.6              0.00               0.0  0.994752  1.0  13.850949   
3        0.6              0.00               0.0  0.991631  1.0  13.628501   
4        0.6              0.00               0.0  0.988107  1.0  13.398817   

   apx      ajxcb       ajxx       Ax  taxa_juros_cob  taxa_juros_det  
0  1.0  13.189854  12.124317  0.23067          0.0551          0.0551  
1  1.0   0.000000   0.000000  0.00000          0.0551          0.0551  
2  1.0   0.000000   0.000000  0.00000          0.0551          0.0551  
3  1.0   0.000000   0.000000  0.00000          0.0551          0.0551  
4  1.0   0.000000   0.000000  0.00000          0.0551          0.0551

In [25]:
for a in range(0, len(ativo_fluxo_atc.iloc[0])):
#     print(row['tCobertura'], row['tDeterministico'])
    if (CdPlanBen == 1):
#         if (ativo_fluxo_atc.iloc[a, 'tCobertura'] == ativo_fluxo_atc.iloc[a, 'tDeterministico']):
#             t_vt = 0
#             ativo_fluxo_atc.iloc[a, 'beneficio_atc'] = max(0, ativo_fluxo_atc.iloc[a, 'BenTotCobAtc'] / FtBenEnti)
#         else:
#             ativo_fluxo_atc.iloc[a, 'beneficio_atc'] = max(0, ativo_fluxo_atc.iloc[a - 1, 'beneficio_atc'] * (1 + PrTxBenef))

#             ativo_fluxo_atc.iloc[a, 'contribuicao_atc'] = max(0, GetContribuicao(ativo_fluxo_atc.iloc[a, 'beneficio_atc']))
#             ativo_fluxo_atc.iloc[a, 'pagamento_atc'] = max(0, (ativo_fluxo_atc.iloc[a, 'beneficio_atc'] - ativo_fluxo_atc.iloc[a, 'contribuicao_atc']) * ativo_fluxo_atc.iloc[a, 'apx'] * NroBenAno)
#             ativo_fluxo_atc.iloc[a, 'despesa_total_atc'] = max(0, (ativo_fluxo_atc.iloc[a, 'beneficio_atc'] * ativo_fluxo_atc.iloc[a, 'apx'] * NroBenAno * ativo_fluxo_atc.iloc[a, 'px'] * ativo_fluxo_atc.iloc[a, 'pxs']))
#             ativo_fluxo_atc.iloc[a, 'receita_total_atc'] = max(0, (ativo_fluxo_atc.iloc[a, 'contribuicao_atc'] * ativo_fluxo_atc.iloc[a, 'apx'] * NroBenAno * ativo_fluxo_atc.iloc[a, 'px'] * ativo_fluxo_atc.iloc[a, 'pxs']))
#             ativo_fluxo_atc.iloc[a, 'despesa_atc'] = max(0, ativo_fluxo_atc.iloc[a, 'despesa_total_atc'] - ativo_fluxo_atc.iloc[a, 'receita_total_atc'])
    else:
        if (ativo_fluxo_atc.iloc[a, 'tCobertura'] == ativo_fluxo_atc.iloc[a, 'tDeterministico']):
            t_vt = 0
            ativo_fluxo_atc.iloc[a, 'pagamento_atc'] = max(0, (ativo_fluxo_atc.iloc[a, 'BenLiqCobAtc'] / FtBenEnti) * ativo_fluxo_atc.iloc[a, 'apx'] * NroBenAno)

            if (CdPlanBen == 2):
#                 ativo_fluxo_atc.iloc[a, 'despesa_bua_atc'] = max(0, ((ativo_fluxo_atc.iloc[a, 'BenTotCobAtc'] * (axcb[a] + &CtFamPens. * PrbCasado[a] * (ajxcb[a] - ajxx[a])) * &NroBenAno.) + ((BenTotCobAtc[a] / &FtBenEnti.) * (ax[a] * &peculioMorteAssistido.))) * apx[a] * &percentualSaqueBUA. * &percentualBUA., 0.01));
            else
                ativo_fluxo_atc.iloc[a, 'despesa_bua_atc'] = max(0, (ativo_fluxo_atc.iloc[a, 'VlSdoConPartEvol'] + ativo_fluxo_atc.iloc[a, 'VlSdoConPatrEvol']) * ativo_fluxo_atc.iloc[a, 'apx'] * percentualSaqueBUA * percentualBUA)
        else:
            ativo_fluxo_atc.iloc[a, 'pagamento_atc'] = max(0, ativo_fluxo_atc.iloc[a - 1, 'pagamento_atc'] * (1 + PrTxBenef))
#             despesa_total_atc[a] = max(0, round((pagamento_atc[a] + despesa_bua_atc[a]) * px[a] * pxs[a], 0.01));
#             despesa_atc[a] = despesa_total_atc[a];

#     v[a] = max(0, 1 / ((1 + taxa_juros_cob[a]) ** tCobertura[a]));
#     vt[a] = max(0, 1 / ((1 + taxa_juros_det[a]) ** t_vt));

#     if (tCobertura[a] = tDeterministico[a]) then
#         despesa_vp_atc[a] = max(0, round(((pagamento_atc[a] * px[a] * vt[a] * &FtBenEnti.) - (&Fb. * pagamento_atc[a] * &FtBenEnti.)) * pxs[a] * v[a] + despesa_bua_atc[a] * v[a] * pxs[a], 0.01));
#     else
#         despesa_vp_atc[a] = max(0, round(pagamento_atc[a] * px[a] * vt[a] * pxs[a] * v[a] * &FtBenEnti., 0.01));

#     t_vt = t_vt + 1;

0.0 0.0
0.0 1.0
0.0 2.0
0.0 3.0
0.0 4.0
0.0 5.0
0.0 6.0
0.0 7.0
0.0 8.0
0.0 9.0
0.0 10.0
0.0 11.0
0.0 12.0
0.0 13.0
0.0 14.0
0.0 15.0
0.0 16.0
0.0 17.0
0.0 18.0
0.0 19.0
0.0 20.0
0.0 21.0
0.0 22.0
0.0 23.0
0.0 24.0
0.0 25.0
0.0 26.0
0.0 27.0
0.0 28.0
0.0 29.0
0.0 30.0
0.0 31.0
0.0 32.0
0.0 33.0
0.0 34.0
0.0 35.0
0.0 36.0
0.0 37.0
0.0 38.0
0.0 39.0
0.0 40.0
0.0 41.0
0.0 42.0
0.0 43.0
0.0 44.0
0.0 45.0
0.0 46.0
0.0 47.0
0.0 48.0
0.0 49.0
0.0 50.0
0.0 51.0
0.0 52.0
0.0 53.0
0.0 54.0
0.0 55.0
0.0 56.0
0.0 57.0
0.0 58.0
0.0 59.0
0.0 60.0
0.0 61.0
0.0 62.0
0.0 63.0
0.0 64.0
0.0 65.0
0.0 66.0
0.0 67.0
0.0 68.0
0.0 69.0
1.0 1.0
1.0 2.0
1.0 3.0
1.0 4.0
1.0 5.0
1.0 6.0
1.0 7.0
1.0 8.0
1.0 9.0
1.0 10.0
1.0 11.0
1.0 12.0
1.0 13.0
1.0 14.0
1.0 15.0
1.0 16.0
1.0 17.0
1.0 18.0
1.0 19.0
1.0 20.0
1.0 21.0
1.0 22.0
1.0 23.0
1.0 24.0
1.0 25.0
1.0 26.0
1.0 27.0
1.0 28.0
1.0 29.0
1.0 30.0
1.0 31.0
1.0 32.0
1.0 33.0
1.0 34.0
1.0 35.0
1.0 36.0
1.0 37.0
1.0 38.0
1.0 39.0
1.0 40.0
1.0 41.0
1.0 42.0
1.0 43.0
1.

27.0 56.0
27.0 57.0
27.0 58.0
27.0 59.0
27.0 60.0
27.0 61.0
27.0 62.0
27.0 63.0
27.0 64.0
27.0 65.0
27.0 66.0
27.0 67.0
27.0 68.0
27.0 69.0
28.0 28.0
28.0 29.0
28.0 30.0
28.0 31.0
28.0 32.0
28.0 33.0
28.0 34.0
28.0 35.0
28.0 36.0
28.0 37.0
28.0 38.0
28.0 39.0
28.0 40.0
28.0 41.0
28.0 42.0
28.0 43.0
28.0 44.0
28.0 45.0
28.0 46.0
28.0 47.0
28.0 48.0
28.0 49.0
28.0 50.0
28.0 51.0
28.0 52.0
28.0 53.0
28.0 54.0
28.0 55.0
28.0 56.0
28.0 57.0
28.0 58.0
28.0 59.0
28.0 60.0
28.0 61.0
28.0 62.0
28.0 63.0
28.0 64.0
28.0 65.0
28.0 66.0
28.0 67.0
28.0 68.0
28.0 69.0
29.0 29.0
29.0 30.0
29.0 31.0
29.0 32.0
29.0 33.0
29.0 34.0
29.0 35.0
29.0 36.0
29.0 37.0
29.0 38.0
29.0 39.0
29.0 40.0
29.0 41.0
29.0 42.0
29.0 43.0
29.0 44.0
29.0 45.0
29.0 46.0
29.0 47.0
29.0 48.0
29.0 49.0
29.0 50.0
29.0 51.0
29.0 52.0
29.0 53.0
29.0 54.0
29.0 55.0
29.0 56.0
29.0 57.0
29.0 58.0
29.0 59.0
29.0 60.0
29.0 61.0
29.0 62.0
29.0 63.0
29.0 64.0
29.0 65.0
29.0 66.0
29.0 67.0
29.0 68.0
29.0 69.0
30.0 30.0
30.0 31.0
30.0 32.0


1.0 59.0
1.0 60.0
1.0 61.0
1.0 62.0
1.0 63.0
1.0 64.0
1.0 65.0
1.0 66.0
1.0 67.0
2.0 2.0
2.0 3.0
2.0 4.0
2.0 5.0
2.0 6.0
2.0 7.0
2.0 8.0
2.0 9.0
2.0 10.0
2.0 11.0
2.0 12.0
2.0 13.0
2.0 14.0
2.0 15.0
2.0 16.0
2.0 17.0
2.0 18.0
2.0 19.0
2.0 20.0
2.0 21.0
2.0 22.0
2.0 23.0
2.0 24.0
2.0 25.0
2.0 26.0
2.0 27.0
2.0 28.0
2.0 29.0
2.0 30.0
2.0 31.0
2.0 32.0
2.0 33.0
2.0 34.0
2.0 35.0
2.0 36.0
2.0 37.0
2.0 38.0
2.0 39.0
2.0 40.0
2.0 41.0
2.0 42.0
2.0 43.0
2.0 44.0
2.0 45.0
2.0 46.0
2.0 47.0
2.0 48.0
2.0 49.0
2.0 50.0
2.0 51.0
2.0 52.0
2.0 53.0
2.0 54.0
2.0 55.0
2.0 56.0
2.0 57.0
2.0 58.0
2.0 59.0
2.0 60.0
2.0 61.0
2.0 62.0
2.0 63.0
2.0 64.0
2.0 65.0
2.0 66.0
2.0 67.0
3.0 3.0
3.0 4.0
3.0 5.0
3.0 6.0
3.0 7.0
3.0 8.0
3.0 9.0
3.0 10.0
3.0 11.0
3.0 12.0
3.0 13.0
3.0 14.0
3.0 15.0
3.0 16.0
3.0 17.0
3.0 18.0
3.0 19.0
3.0 20.0
3.0 21.0
3.0 22.0
3.0 23.0
3.0 24.0
3.0 25.0
3.0 26.0
3.0 27.0
3.0 28.0
3.0 29.0
3.0 30.0
3.0 31.0
3.0 32.0
3.0 33.0
3.0 34.0
3.0 35.0
3.0 36.0
3.0 37.0
3.0 38.0
3.0 39.0
3.0 40.

19.0 23.0
19.0 24.0
19.0 25.0
19.0 26.0
19.0 27.0
19.0 28.0
19.0 29.0
19.0 30.0
19.0 31.0
19.0 32.0
19.0 33.0
19.0 34.0
19.0 35.0
19.0 36.0
19.0 37.0
19.0 38.0
19.0 39.0
19.0 40.0
19.0 41.0
19.0 42.0
19.0 43.0
19.0 44.0
19.0 45.0
19.0 46.0
19.0 47.0
19.0 48.0
19.0 49.0
19.0 50.0
19.0 51.0
19.0 52.0
19.0 53.0
19.0 54.0
19.0 55.0
19.0 56.0
19.0 57.0
19.0 58.0
19.0 59.0
19.0 60.0
19.0 61.0
19.0 62.0
19.0 63.0
19.0 64.0
19.0 65.0
19.0 66.0
19.0 67.0
20.0 20.0
20.0 21.0
20.0 22.0
20.0 23.0
20.0 24.0
20.0 25.0
20.0 26.0
20.0 27.0
20.0 28.0
20.0 29.0
20.0 30.0
20.0 31.0
20.0 32.0
20.0 33.0
20.0 34.0
20.0 35.0
20.0 36.0
20.0 37.0
20.0 38.0
20.0 39.0
20.0 40.0
20.0 41.0
20.0 42.0
20.0 43.0
20.0 44.0
20.0 45.0
20.0 46.0
20.0 47.0
20.0 48.0
20.0 49.0
20.0 50.0
20.0 51.0
20.0 52.0
20.0 53.0
20.0 54.0
20.0 55.0
20.0 56.0
20.0 57.0
20.0 58.0
20.0 59.0
20.0 60.0
20.0 61.0
20.0 62.0
20.0 63.0
20.0 64.0
20.0 65.0
20.0 66.0
20.0 67.0
21.0 21.0
21.0 22.0
21.0 23.0
21.0 24.0
21.0 25.0
21.0 26.0
21.0 27.0


47.0 61.0
47.0 62.0
47.0 63.0
47.0 64.0
47.0 65.0
47.0 66.0
47.0 67.0
48.0 48.0
48.0 49.0
48.0 50.0
48.0 51.0
48.0 52.0
48.0 53.0
48.0 54.0
48.0 55.0
48.0 56.0
48.0 57.0
48.0 58.0
48.0 59.0
48.0 60.0
48.0 61.0
48.0 62.0
48.0 63.0
48.0 64.0
48.0 65.0
48.0 66.0
48.0 67.0
49.0 49.0
49.0 50.0
49.0 51.0
49.0 52.0
49.0 53.0
49.0 54.0
49.0 55.0
49.0 56.0
49.0 57.0
49.0 58.0
49.0 59.0
49.0 60.0
49.0 61.0
49.0 62.0
49.0 63.0
49.0 64.0
49.0 65.0
49.0 66.0
49.0 67.0
50.0 50.0
50.0 51.0
50.0 52.0
50.0 53.0
50.0 54.0
50.0 55.0
50.0 56.0
50.0 57.0
50.0 58.0
50.0 59.0
50.0 60.0
50.0 61.0
50.0 62.0
50.0 63.0
50.0 64.0
50.0 65.0
50.0 66.0
50.0 67.0
51.0 51.0
51.0 52.0
51.0 53.0
51.0 54.0
51.0 55.0
51.0 56.0
51.0 57.0
51.0 58.0
51.0 59.0
51.0 60.0
51.0 61.0
51.0 62.0
51.0 63.0
51.0 64.0
51.0 65.0
51.0 66.0
51.0 67.0
52.0 52.0
52.0 53.0
52.0 54.0
52.0 55.0
52.0 56.0
52.0 57.0
52.0 58.0
52.0 59.0
52.0 60.0
52.0 61.0
52.0 62.0
52.0 63.0
52.0 64.0
52.0 65.0
52.0 66.0
52.0 67.0
53.0 53.0
53.0 54.0
53.0 55.0


...

19.0 63.0
19.0 64.0
19.0 65.0
19.0 66.0
19.0 67.0
19.0 68.0
19.0 69.0
19.0 70.0
20.0 20.0
20.0 21.0
20.0 22.0
20.0 23.0
20.0 24.0
20.0 25.0
20.0 26.0
20.0 27.0
20.0 28.0
20.0 29.0
20.0 30.0
20.0 31.0
20.0 32.0
20.0 33.0
20.0 34.0
20.0 35.0
20.0 36.0
20.0 37.0
20.0 38.0
20.0 39.0
20.0 40.0
20.0 41.0
20.0 42.0
20.0 43.0
20.0 44.0
20.0 45.0
20.0 46.0
20.0 47.0
20.0 48.0
20.0 49.0
20.0 50.0
20.0 51.0
20.0 52.0
20.0 53.0
20.0 54.0
20.0 55.0
20.0 56.0
20.0 57.0
20.0 58.0
20.0 59.0
20.0 60.0
20.0 61.0
20.0 62.0
20.0 63.0
20.0 64.0
20.0 65.0
20.0 66.0
20.0 67.0
20.0 68.0
20.0 69.0
20.0 70.0
21.0 21.0
21.0 22.0
21.0 23.0
21.0 24.0
21.0 25.0
21.0 26.0
21.0 27.0
21.0 28.0
21.0 29.0
21.0 30.0
21.0 31.0
21.0 32.0
21.0 33.0
21.0 34.0
21.0 35.0
21.0 36.0
21.0 37.0
21.0 38.0
21.0 39.0
21.0 40.0
21.0 41.0
21.0 42.0
21.0 43.0
21.0 44.0
21.0 45.0
21.0 46.0
21.0 47.0
21.0 48.0
21.0 49.0
21.0 50.0
21.0 51.0
21.0 52.0
21.0 53.0
21.0 54.0
21.0 55.0
21.0 56.0
21.0 57.0
21.0 58.0
21.0 59.0
21.0 60.0
21.0 61.0


45.0 66.0
45.0 67.0
45.0 68.0
45.0 69.0
45.0 70.0
46.0 46.0
46.0 47.0
46.0 48.0
46.0 49.0
46.0 50.0
46.0 51.0
46.0 52.0
46.0 53.0
46.0 54.0
46.0 55.0
46.0 56.0
46.0 57.0
46.0 58.0
46.0 59.0
46.0 60.0
46.0 61.0
46.0 62.0
46.0 63.0
46.0 64.0
46.0 65.0
46.0 66.0
46.0 67.0
46.0 68.0
46.0 69.0
46.0 70.0
47.0 47.0
47.0 48.0
47.0 49.0
47.0 50.0
47.0 51.0
47.0 52.0
47.0 53.0
47.0 54.0
47.0 55.0
47.0 56.0
47.0 57.0
47.0 58.0
47.0 59.0
47.0 60.0
47.0 61.0
47.0 62.0
47.0 63.0
47.0 64.0
47.0 65.0
47.0 66.0
47.0 67.0
47.0 68.0
47.0 69.0
47.0 70.0
48.0 48.0
48.0 49.0
48.0 50.0
48.0 51.0
48.0 52.0
48.0 53.0
48.0 54.0
48.0 55.0
48.0 56.0
48.0 57.0
48.0 58.0
48.0 59.0
48.0 60.0
48.0 61.0
48.0 62.0
48.0 63.0
48.0 64.0
48.0 65.0
48.0 66.0
48.0 67.0
48.0 68.0
48.0 69.0
48.0 70.0
49.0 49.0
49.0 50.0
49.0 51.0
49.0 52.0
49.0 53.0
49.0 54.0
49.0 55.0
49.0 56.0
49.0 57.0
49.0 58.0
49.0 59.0
49.0 60.0
49.0 61.0
49.0 62.0
49.0 63.0
49.0 64.0
49.0 65.0
49.0 66.0
49.0 67.0
49.0 68.0
49.0 69.0
49.0 70.0
50.0 50.0


8.0 52.0
8.0 53.0
8.0 54.0
8.0 55.0
8.0 56.0
8.0 57.0
8.0 58.0
8.0 59.0
8.0 60.0
8.0 61.0
8.0 62.0
8.0 63.0
8.0 64.0
8.0 65.0
8.0 66.0
8.0 67.0
8.0 68.0
9.0 9.0
9.0 10.0
9.0 11.0
9.0 12.0
9.0 13.0
9.0 14.0
9.0 15.0
9.0 16.0
9.0 17.0
9.0 18.0
9.0 19.0
9.0 20.0
9.0 21.0
9.0 22.0
9.0 23.0
9.0 24.0
9.0 25.0
9.0 26.0
9.0 27.0
9.0 28.0
9.0 29.0
9.0 30.0
9.0 31.0
9.0 32.0
9.0 33.0
9.0 34.0
9.0 35.0
9.0 36.0
9.0 37.0
9.0 38.0
9.0 39.0
9.0 40.0
9.0 41.0
9.0 42.0
9.0 43.0
9.0 44.0
9.0 45.0
9.0 46.0
9.0 47.0
9.0 48.0
9.0 49.0
9.0 50.0
9.0 51.0
9.0 52.0
9.0 53.0
9.0 54.0
9.0 55.0
9.0 56.0
9.0 57.0
9.0 58.0
9.0 59.0
9.0 60.0
9.0 61.0
9.0 62.0
9.0 63.0
9.0 64.0
9.0 65.0
9.0 66.0
9.0 67.0
9.0 68.0
10.0 10.0
10.0 11.0
10.0 12.0
10.0 13.0
10.0 14.0
10.0 15.0
10.0 16.0
10.0 17.0
10.0 18.0
10.0 19.0
10.0 20.0
10.0 21.0
10.0 22.0
10.0 23.0
10.0 24.0
10.0 25.0
10.0 26.0
10.0 27.0
10.0 28.0
10.0 29.0
10.0 30.0
10.0 31.0
10.0 32.0
10.0 33.0
10.0 34.0
10.0 35.0
10.0 36.0
10.0 37.0
10.0 38.0
10.0 39.0
10.0 40.

28.0 49.0
28.0 50.0
28.0 51.0
28.0 52.0
28.0 53.0
28.0 54.0
28.0 55.0
28.0 56.0
28.0 57.0
28.0 58.0
28.0 59.0
28.0 60.0
28.0 61.0
28.0 62.0
28.0 63.0
28.0 64.0
28.0 65.0
28.0 66.0
28.0 67.0
28.0 68.0
29.0 29.0
29.0 30.0
29.0 31.0
29.0 32.0
29.0 33.0
29.0 34.0
29.0 35.0
29.0 36.0
29.0 37.0
29.0 38.0
29.0 39.0
29.0 40.0
29.0 41.0
29.0 42.0
29.0 43.0
29.0 44.0
29.0 45.0
29.0 46.0
29.0 47.0
29.0 48.0
29.0 49.0
29.0 50.0
29.0 51.0
29.0 52.0
29.0 53.0
29.0 54.0
29.0 55.0
29.0 56.0
29.0 57.0
29.0 58.0
29.0 59.0
29.0 60.0
29.0 61.0
29.0 62.0
29.0 63.0
29.0 64.0
29.0 65.0
29.0 66.0
29.0 67.0
29.0 68.0
30.0 30.0
30.0 31.0
30.0 32.0
30.0 33.0
30.0 34.0
30.0 35.0
30.0 36.0
30.0 37.0
30.0 38.0
30.0 39.0
30.0 40.0
30.0 41.0
30.0 42.0
30.0 43.0
30.0 44.0
30.0 45.0
30.0 46.0
30.0 47.0
30.0 48.0
30.0 49.0
30.0 50.0
30.0 51.0
30.0 52.0
30.0 53.0
30.0 54.0
30.0 55.0
30.0 56.0
30.0 57.0
30.0 58.0
30.0 59.0
30.0 60.0
30.0 61.0
30.0 62.0
30.0 63.0
30.0 64.0
30.0 65.0
30.0 66.0
30.0 67.0
30.0 68.0
31.0 31.0


KeyboardInterrupt: 

In [15]:
ativo['beneficio_total_atc'] = ativo.apply(calcular_beneficio_total_atc, axis = 1)

In [16]:
ativo['contribuicao_beneficio_atc'] = [calcular_contribuicao(value, teto_contribuicao_inss, faixa_1, faixa_2, faixa_3) for value in ativo['beneficio_total_atc']]

In [17]:
ativo['beneficio_liquido_atc'] = [calcular_beneficio_liquido_atc(b, c, perct_opcao_bua, perct_saque_bua) for b, c in zip(ativo['beneficio_total_atc'], ativo['contribuicao_beneficio_atc'])]

In [ ]:
#  ativo[['ID_PARTICIPANTE', 't', 'beneficio_total_atc', 'contribuicao_beneficio_atc', 'beneficio_liquido_atc']]